In [1]:
import pyscenic
print(pyscenic.__version__)

0.12.1


In [2]:
import dask
print(dask.__version__)

2024.2.1


In [3]:
import numpy as np
import pandas as pd
!pip install scanpy
import scanpy as sc
!pip install igraph
import igraph

import anndata
from scipy import io
from scipy.sparse import coo_matrix, csr_matrix
import os

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com


In [4]:
import os
import glob
import pickle

In [5]:
from dask.diagnostics import ProgressBar

In [6]:
from arboreto.utils import load_tf_names
from arboreto.algo import grnboost2

In [7]:
from ctxcore.rnkdb import FeatherRankingDatabase as RankingDatabase
from pyscenic.utils import modules_from_adjacencies, load_motifs
from pyscenic.prune import prune2df, df2regulons
from pyscenic.aucell import aucell

In [8]:
import seaborn as sns

In [9]:
ex_matrix = pd.read_csv("/home/shruti/Documents/shruti/pySCENIC/beta2_RC/expression_matrix_beta2_RC.txt", sep='\t', header=0, index_col=0).T

In [10]:
ex_matrix.shape

(8275, 17576)

In [11]:
tf_names = load_tf_names("/home/shruti/Documents/shruti/pySCENIC/allTFs_mm.txt")

In [12]:
import os
import glob

# Set the path to the directory containing your feather files
DATABASES_GLOB = r"/home/shruti/Documents/shruti/pySCENIC/cisTARGETDATABASE_v2/*.feather"  # Assuming the files have a .feather extension

# Use glob to find all matching files
db_fnames = glob.glob(DATABASES_GLOB)

# Debugging: Print what glob returns to check if the files are being found
print("Files found:", db_fnames)

# Define the function to extract the base name without extension
def name(fname):
    return os.path.splitext(os.path.basename(fname))[0]

# Create instances of FeatherRankingDatabase for each file found
dbs = [RankingDatabase(fname=fname, name=name(fname)) for fname in db_fnames]

# Output the list of databases
print(dbs)

Files found: ['/home/shruti/Documents/shruti/pySCENIC/cisTARGETDATABASE_v2/mm9-500bp-upstream-10species.mc9nr.genes_vs_motifs.rankings.feather', '/home/shruti/Documents/shruti/pySCENIC/cisTARGETDATABASE_v2/mm9-tss-centered-10kb-10species.mc9nr.genes_vs_motifs.rankings.feather', '/home/shruti/Documents/shruti/pySCENIC/cisTARGETDATABASE_v2/mm9-500bp-upstream-7species.mc9nr.genes_vs_motifs.rankings.feather', '/home/shruti/Documents/shruti/pySCENIC/cisTARGETDATABASE_v2/mm9-tss-centered-10kb-7species.mc9nr.genes_vs_motifs.rankings.feather', '/home/shruti/Documents/shruti/pySCENIC/cisTARGETDATABASE_v2/mm9-tss-centered-5kb-7species.mc9nr.genes_vs_motifs.rankings.feather', '/home/shruti/Documents/shruti/pySCENIC/cisTARGETDATABASE_v2/mm9-tss-centered-5kb-10species.mc9nr.genes_vs_motifs.rankings.feather']
[FeatherRankingDatabase(name="mm9-500bp-upstream-10species.mc9nr.genes_vs_motifs.rankings"), FeatherRankingDatabase(name="mm9-tss-centered-10kb-10species.mc9nr.genes_vs_motifs.rankings"), Feath

In [13]:
wdir = '/home/shruti/Documents/shruti/pySCENIC/beta2_RC'
os.chdir(wdir)

In [14]:
ex_matrix.head()

0610005C13Rik  0610009B22Rik  0610009O20Rik  \
RC-8W-1R_AAAGGTAGTTGAAGTA-1            0.0            0.0            0.0   
RC-8W-1R_AACACACAGAATCTAG-1            0.0            0.0            0.0   
RC-8W-1R_AACGGGATCCTCATAT-1            0.0            0.0            0.0   
RC-8W-1R_ACACAGTTCTACCCAC-1            0.0            0.0            0.0   
RC-8W-1R_ACACGCGTCGCGTTTC-1            0.0            0.0            0.0   

                             0610010F05Rik  0610010K14Rik  0610012G03Rik  \
RC-8W-1R_AAAGGTAGTTGAAGTA-1       0.437581            0.0       0.000000   
RC-8W-1R_AACACACAGAATCTAG-1       0.000000            0.0       0.347193   
RC-8W-1R_AACGGGATCCTCATAT-1       0.000000            0.0       0.000000   
RC-8W-1R_ACACAGTTCTACCCAC-1       0.000000            0.0       0.000000   
RC-8W-1R_ACACGCGTCGCGTTTC-1       0.000000            0.0       0.000000   

                             0610025J13Rik  0610030E20Rik  0610037L13Rik  \
RC-8W-1R_AAAGGTAGTTGAAGTA-1            0.0            0.0       0.710576   
RC-8W-1R_AACACACAGAATCTAG-1            0.0            0.0       0.000000   
RC-8W-1R_AACGGGATCCTCATAT-1            0.0            0.0       0.000000   
RC-8W-1R_ACACAGTTCTACCCAC-1            0.0            0.0       0.000000   
RC-8W-1R_ACACGCGTCGCGTTTC-1            0.0            0.0       0.000000   

                             0610038B21Rik  ...  Wnt6  Xpnpep2  Zcchc13  \
RC-8W-1R_AAAGGTAGTTGAAGTA-1            0.0  ...   0.0      0.0      0.0   
RC-8W-1R_AACACACAGAATCTAG-1            0.0  ...   0.0      0.0      0.0   
RC-8W-1R_AACGGGATCCTCATAT-1            0.0  ...   0.0      0.0      0.0   
RC-8W-1R_ACACAGTTCTACCCAC-1            0.0  ...   0.0      0.0      0.0   
RC-8W-1R_ACACGCGTCGCGTTTC-1            0.0  ...   0.0      0.0      0.0   

                             Zfp385c  Zfp536  Zfp711  Zfp831  Zfp981  Zfp985  \
RC-8W-1R_AAAGGTAGTTGAAGTA-1      0.0     0.0     0.0     0.0     0.0     0.0   
RC-8W-1R_AACACACAGAATCTAG-1      0.0     0.0     0.0     0.0     0.0     0.0   
RC-8W-1R_AACGGGATCCTCATAT-1      0.0     0.0     0.0     0.0     0.0     0.0   
RC-8W-1R_ACACAGTTCTACCCAC-1      0.0     0.0     0.0     0.0     0.0     0.0   
RC-8W-1R_ACACGCGTCGCGTTTC-1      0.0     0.0     0.0     0.0     0.0     0.0   

                             Zpld1  
RC-8W-1R_AAAGGTAGTTGAAGTA-1    0.0  
RC-8W-1R_AACACACAGAATCTAG-1    0.0  
RC-8W-1R_AACGGGATCCTCATAT-1    0.0  
RC-8W-1R_ACACAGTTCTACCCAC-1    0.0  
RC-8W-1R_ACACGCGTCGCGTTTC-1    0.0  

[5 rows x 17576 columns]

In [15]:
!pip install dask-expr==0.5.3 distributed==2024.2.1

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com


In [16]:
from dask import delayed
print(type(delayed(ex_matrix)))

<class 'dask.delayed.DelayedLeaf'>


In [17]:
adjancencies = grnboost2(expression_data=ex_matrix, tf_names=tf_names, verbose=True)

preparing dask client
parsing input
creating dask graph
12 partitions
computing dask graph


/home/shruti/anaconda3/envs/attempt_b/lib/python3.10/site-packages/distributed/client.py:3169: UserWarning: Sending large graph of size 1.03 GiB.
This may cause some slowdown.
Consider scattering data ahead of time and using futures.
  warnings.warn(


shutting down client and local cluster
finished


In [18]:
adjancencies.head()

TF target  importance
772  Rps10  Rps14   24.515472
772  Rps10   Ins1   23.474317
772  Rps10   Ssr4   21.096772
772  Rps10  Rps18   20.724561
772  Rps10   Ins2   19.829201

In [19]:
adjancencies.to_csv("ADJACENCIES_FNAME", index=False, sep='\t')
adjancencies.to_csv("ADJACENCIES_FNAME.csv", index=False)

In [20]:
modules = list(modules_from_adjacencies(adjancencies, ex_matrix))


2024-12-10 11:16:18,439 - pyscenic.utils - INFO - Calculating Pearson correlations.

2024-12-10 11:16:20,470 - pyscenic.utils - WARNING - Note on correlation calculation: the default behaviour for calculating the correlations has changed after pySCENIC verion 0.9.16. Previously, the default was to calculate the correlation between a TF and target gene using only cells with non-zero expression values (mask_dropouts=True). The current default is now to use all cells to match the behavior of the R verision of SCENIC. The original settings can be retained by setting 'rho_mask_dropouts=True' in the modules_from_adjacencies function, or '--mask_dropouts' from the CLI.
	Dropout masking is currently set to [False].

2024-12-10 11:16:39,335 - pyscenic.utils - INFO - Creating modules.


In [21]:
with open("MODULES_FNAME", 'wb') as f:
    pickle.dump(modules, f)

In [22]:
MOTIF_ANNOTATIONS_FNAME = "/home/shruti/Documents/shruti/pySCENIC/motifs-v9-nr.mgi-m0.001-o0.0.tbl"

In [23]:
df = prune2df(dbs, modules, MOTIF_ANNOTATIONS_FNAME)


2024-12-10 11:20:10,228 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Homez could be mapped to mm9-tss-centered-10kb-10species.mc9nr.genes_vs_motifs.rankings. Skipping this module.

2024-12-10 11:20:10,487 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Hoxa3 could be mapped to mm9-tss-centered-10kb-10species.mc9nr.genes_vs_motifs.rankings. Skipping this module.

2024-12-10 11:20:10,554 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Zfp212 could be mapped to mm9-tss-centered-10kb-10species.mc9nr.genes_vs_motifs.rankings. Skipping this module.

2024-12-10 11:20:10,751 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Zfp213 could be mapped to mm9-tss-centered-10kb-10species.mc9nr.genes_vs_motifs.rankings. Skipping this module.

2024-12-10 11:20:10,872 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for Zfp217 could be mapped to mm9-tss-centered-10kb-10spec

In [24]:
df.head()

Enrichment            \
                                                  AUC       NES   
TF     MotifID                                                    
Bclaf1 taipale__ETS1_full_ACCGGAARYN         0.052922  3.021904   
       taipale__FLI1_full_ACCGGAARYN         0.053150  3.050437   
       hdpi__ELF2                            0.054836  3.261524   
       dbcorrdb__ZNF143__ENCSR000EGP_1__m3   0.054797  3.256636   
       dbcorrdb__POLR2A__ENCSR000DMZ_1__m1   0.055885  3.392825   

                                                                  \
                                           MotifSimilarityQvalue   
TF     MotifID                                                     
Bclaf1 taipale__ETS1_full_ACCGGAARYN                    0.000914   
       taipale__FLI1_full_ACCGGAARYN                    0.000901   
       hdpi__ELF2                                       0.000732   
       dbcorrdb__ZNF143__ENCSR000EGP_1__m3              0.000451   
       dbcorrdb__POLR2A__ENCSR000DMZ_1__m1              0.000428   

                                                                \
                                           OrthologousIdentity   
TF     MotifID                                                   
Bclaf1 taipale__ETS1_full_ACCGGAARYN                  0.954348   
       taipale__FLI1_full_ACCGGAARYN                  0.955386   
       hdpi__ELF2                                     0.955386   
       dbcorrdb__ZNF143__ENCSR000EGP_1__m3            0.955386   
       dbcorrdb__POLR2A__ENCSR000DMZ_1__m1            0.955386   

                                                                                               \
                                                                                   Annotation   
TF     MotifID                                                                                  
Bclaf1 taipale__ETS1_full_ACCGGAARYN        motif similar to transfac_pro__M04704 ('V$BCLA...   
       taipale__FLI1_full_ACCGGAARYN        gene is orthologous to ENSG00000029363 in H. s...   
       hdpi__ELF2                           gene is orthologous to ENSG00000029363 in H. s...   
       dbcorrdb__ZNF143__ENCSR000EGP_1__m3  gene is orthologous to ENSG00000029363 in H. s...   
       dbcorrdb__POLR2A__ENCSR000DMZ_1__m1  gene is orthologous to ENSG00000029363 in H. s...   

                                                                                               \
                                                                                      Context   
TF     MotifID                                                                                  
Bclaf1 taipale__ETS1_full_ACCGGAARYN        frozenset({'weight>75.0%', 'activating', 'mm9-...   
       taipale__FLI1_full_ACCGGAARYN        frozenset({'weight>75.0%', 'activating', 'mm9-...   
       hdpi__ELF2                           frozenset({'weight>75.0%', 'activating', 'mm9-...   
       dbcorrdb__ZNF143__ENCSR000EGP_1__m3  frozenset({'weight>75.0%', 'activating', 'mm9-...   
       dbcorrdb__POLR2A__ENCSR000DMZ_1__m1  frozenset({'weight>75.0%', 'activating', 'mm9-...   

                                                                                               \
                                                                                  TargetGenes   
TF     MotifID                                                                                  
Bclaf1 taipale__ETS1_full_ACCGGAARYN        [('Ep300', np.float64(0.3525584928455913)), ('...   
       taipale__FLI1_full_ACCGGAARYN        [('Nrip1', np.float64(0.9425634278564845)), ('...   
       hdpi__ELF2                           [('Clock', np.float64(1.335495447135766)), ('O...   
       dbcorrdb__ZNF143__ENCSR000EGP_1__m3  [('Zc3h4', np.float64(0.6902391072983675)), ('...   
       dbcorrdb__POLR2A__ENCSR000DMZ_1__m1  [('Appl2', np.float64(0.69798087532751)), ('At...   

                                                      
                                           Ran

In [25]:
df.to_csv("MOTIFS_FNAME")
df.to_csv("MOTIFS_FNAME.csv")

In [26]:
regulons = df2regulons(df)

Create regulons from a dataframe of enriched features.
Additional columns saved: []


In [27]:
with open("REGULONS_FNAME", 'wb') as f:
    pickle.dump(regulons, f)

#with open(REGULONS_FNAME, 'rb') as f:
#    regulons = pickle.load(f)


In [28]:
print(regulons)

[Regulon(name='1810024B03Rik(+)', gene2weight=frozendict.frozendict({'[': 1.0, '(': 1.0, "'": 1.0, 'S': 1.0, 'l': 1.0, 'c': 1.0, '3': 1.0, '5': 1.0, 'f': 1.0, ',': 1.0, ' ': 1.0, 'n': 1.0, 'p': 1.0, '.': 1.0, 'o': 1.0, 'a': 1.0, 't': 1.0, '6': 1.0, '4': 1.0, '1': 1.0, '8': 1.0, '2': 1.0, '7': 1.0, '9': 1.0, ')': 1.0, 'L': 1.0, 'i': 1.0, 'x': 1.0, '0': 1.0, 'G': 1.0, 'P': 1.0, 'k': 1.0, 'r': 1.0, ']': 1.0, 'N': 1.0, 's': 1.0, 'R': 1.0, 'g': 1.0, 'U': 1.0, 'B': 1.0, 'A': 1.0, 'h': 1.0}), gene2occurrence=frozendict.frozendict({}), transcription_factor='1810024B03Rik', context=frozenset({'dbcorrdb__POLR3G__ENCSR000EHQ_1__m1.png', 'activating'}), score=0.14623498243299785, nes=0.0, orthologous_identity=0.0, similarity_qvalue=0.0, annotation=''), Regulon(name='Ar(+)', gene2weight=frozendict.frozendict({'[': 1.0, '(': 1.0, "'": 1.0, 'S': 1.0, 'l': 1.0, 'c': 1.0, '2': 1.0, 'a': 1.0, ',': 1.0, ' ': 1.0, 'n': 1.0, 'p': 1.0, '.': 1.0, 'f': 1.0, 'o': 1.0, 't': 1.0, '6': 1.0, '4': 1.0, '0': 1.0, '3

In [29]:
auc_mtx = aucell(ex_matrix, regulons, num_workers=1)

  0%|                                                                                                                                                                                      | 0/196 [00:00<?, ?it/s]Less than 80% of the genes in 1810024B03Rik(+) are present in the expression matrix.
Less than 80% of the genes in Ar(+) are present in the expression matrix.
Less than 80% of the genes in Ascc1(+) are present in the expression matrix.
Less than 80% of the genes in Atf1(+) are present in the expression matrix.
Less than 80% of the genes in Atf2(+) are present in the expression matrix.
Less than 80% of the genes in Atf4(+) are present in the expression matrix.
Less than 80% of the genes in Atf5(+) are present in the expression matrix.
Less than 80% of the genes in Atf6(+) are present in the expression matrix.
Less than 80% of the genes in Atf6b(+) are present in the expression matrix.
Less than 80% of the genes in Bach1(+) are present in the expression matrix.
Less than 80% of th

In [30]:
auc_mtx.shape

(8275, 196)

In [31]:
auc_mtx.head()

Regulon                       1810024B03Rik(+)  Ar(+)  Ascc1(+)  Atf1(+)  \
Cell                                                                       
RC-14W-1R_AAGGAATAGCGCCCAT-1               0.0    0.0       0.0      0.0   
RC-14W-1R_ACTCTCGCACTTTATC-1               0.0    0.0       0.0      0.0   
RC-14W-1R_AGAAATGGTTGTCATG-1               0.0    0.0       0.0      0.0   
RC-14W-1R_AGTACTGCAGAGAAAG-1               0.0    0.0       0.0      0.0   
RC-14W-1R_ATGCGATAGATAGCTA-1               0.0    0.0       0.0      0.0   

Regulon                       Atf2(+)  Atf4(+)  Atf5(+)  Atf6(+)  Atf6b(+)  \
Cell                                                                         
RC-14W-1R_AAGGAATAGCGCCCAT-1      0.0      0.0      0.0      0.0       0.0   
RC-14W-1R_ACTCTCGCACTTTATC-1      0.0      0.0      0.0      0.0       0.0   
RC-14W-1R_AGAAATGGTTGTCATG-1      0.0      0.0      0.0      0.0       0.0   
RC-14W-1R_AGTACTGCAGAGAAAG-1      0.0      0.0      0.0      0.0       0.0   
RC-14W-1R_ATGCGATAGATAGCTA-1      0.0      0.0      0.0      0.0       0.0   

Regulon                       Bach1(+)  ...  Zfp382(+)  Zfp410(+)  Zfp62(+)  \
Cell                                    ...                                   
RC-14W-1R_AAGGAATAGCGCCCAT-1       0.0  ...        0.0        0.0       0.0   
RC-14W-1R_ACTCTCGCACTTTATC-1       0.0  ...        0.0        0.0       0.0   
RC-14W-1R_AGAAATGGTTGTCATG-1       0.0  ...        0.0        0.0       0.0   
RC-14W-1R_AGTACTGCAGAGAAAG-1       0.0  ...        0.0        0.0       0.0   
RC-14W-1R_ATGCGATAGATAGCTA-1       0.0  ...        0.0        0.0       0.0   

Regulon                       Zfp664(+)  Zfp667(+)  Zfp704(+)  Zfx(+)  \
Cell                                                                    
RC-14W-1R_AAGGAATAGCGCCCAT-1        0.0        0.0        0.0     0.0   
RC-14W-1R_ACTCTCGCACTTTATC-1        0.0        0.0        0.0     0.0   
RC-14W-1R_AGAAATGGTTGTCATG-1        0.0        0.0        0.0     0.0   
RC-14W-1R_AGTACTGCAGAGAAAG-1        0.0        0.0        0.0     0.0   
RC-14W-1R_ATGCGATAGATAGCTA-1        0.0        0.0        0.0     0.0   

Regulon                       Zkscan14(+)  Zscan2(+)  Zxdb(+)  
Cell                                                           
RC-14W-1R_AAGGAATAGCGCCCAT-1          0.0        0.0      0.0  
RC-14W-1R_ACTCTCGCACTTTATC-1          0.0        0.0      0.0  
RC-14W-1R_AGAAATGGTTGTCATG-1          0.0        0.0      0.0  
RC-14W-1R_AGTACTGCAGAGAAAG-1          0.0        0.0      0.0  
RC-14W-1R_ATGCGATAGATAGCTA-1          0.0        0.0      0.0  

[5 rows x 196 columns]

In [32]:
auc_mtx.to_csv("auc_mtx")
auc_mtx.to_csv("auc_mtx.csv")